In [1]:
import sys
import json
import pickle

In [2]:
sys.path.append('/Users/mahbubcseju/Desktop/projects/vul_detect')

In [3]:
with open("../../data/devign/test.jsonl", 'r') as f:
    data = []
    for  line in f:
        try:
            data.append(json.loads(line.strip()))
        except Exception as e:
            print(e)


In [4]:
df = pickle.load(open('explanation_devign.pkl', 'rb'))

In [5]:
import re
def cleaner(code):
    ## Remove code comments
    pat = re.compile(r'(/\*([^*]|(\*+[^*/]))*\*+/)|(//.*)')
    code = re.sub(pat,'',code)
    code = re.sub('\n','',code)
    code = re.sub('\t','',code)
    return(code)

In [6]:
data_lines = []
for orginal, explanation_ in zip(data, df):
    # if orginal['idx'] != 26489:
    #     continue
    lines = orginal['func'].split("\n")
    # print(orginal['func'])
    explanation = explanation_['sentence']
    # print(explanation.tokens)
    # print(len(lines))
    ptr = 0
    final_lines = []
    cur_line = []
    line_ptr = cleaner(lines[ptr])
    for word in explanation.tokens:
        # print(word)
        # print("Word: ", word, "Line: ", line_ptr)
        while word not in line_ptr:
            # print("line: ", line_ptr,"word: ",  word)
            final_lines.append(cur_line)
            cur_line = []
            ptr += 1
            line_ptr = cleaner(line_ptr + lines[ptr])
        # print(line_ptr, word)
        # print("Found: ", line_ptr, "word ", word)
        line_ptr = line_ptr[line_ptr.index(word) + len(word):]
        # print("next:", line_ptr)
        cur_line.append(word)
    while ptr < len(lines):
        final_lines.append(cur_line)
        cur_line = []
        ptr += 1
    
    assert len(lines) == len(final_lines)
    tokens = [tok for line in final_lines for tok in line]
    assert tokens == explanation.tokens
    data_lines.append(final_lines)
    # print(final_lines, len(final_lines))
    # break

In [7]:
data_lines

[[['int',
   'ff',
   '_get_',
   'wa',
   'v_',
   'header',
   '(',
   'AV',
   'Format',
   'Context',
   '*',
   's',
   ',',
   'AV',
   'IO',
   'Context',
   '*',
   'pb',
   ','],
  [],
  ['AVCodec',
   'Context',
   '*',
   'codec',
   ',',
   'int',
   'size',
   ',',
   'int',
   'big_',
   'endian',
   ')'],
  [],
  ['{'],
  [],
  ['int', 'id', ';'],
  [],
  ['uint64_t', 'bitrate', ';'],
  [],
  [],
  [],
  ['if', '(', 'size', '<', '14', ')', '{'],
  [],
  ['av',
   'priv',
   '_request_',
   'sample',
   '(',
   'codec',
   ',',
   '"w',
   'av',
   'header',
   'size',
   '<',
   '14',
   '"',
   ')',
   ';'],
  [],
  ['return', 'AV', 'ERROR_INVALID', 'DATA', ';'],
  [],
  ['}'],
  [],
  [],
  [],
  ['codec',
   '->',
   'codec_',
   'type',
   '=',
   'AV',
   'MEDIA_',
   'TYPE_',
   'AUDIO',
   ';'],
  [],
  ['if', '(', '!', 'big_', 'endian', ')', '{'],
  [],
  ['id', '=', 'avi', 'o_', 'rl', '16', '(', 'pb', ')', ';'],
  [],
  ['if', '(', 'id', '!=', '0x0', '16', '5', 

In [8]:
def get_max_match(original, start_index,  tokens):
    lo = len(original)
    lt = len(tokens)
    ind , max_score = 0, lo
    for i in range(start_index, lo-lt+ 1):
        found = True
        for j in range(lt):
            if  original[i + j] != tokens[j]:
                found = False
        if found:
            return [x for x in range(i, i + lt)]
    return []

In [9]:
def calculate_score(scores, ids):
    sum = 0
    for id in ids:
        sum += scores[id]
    return sum

In [10]:
line_scores = []
for lines, explanation_, data_ in zip(data_lines, df, data):
    explanation = explanation_['sentence']
    scores = []
    start_index = 0
    for line in lines:
        ids = get_max_match(explanation.tokens, start_index, line)
        if ids:
            start_index = ids[-1] + 1
        scores.append(calculate_score(explanation.salience, ids))
    line_scores.append({
        'idx': data_['idx'],
        'scores': scores
    })
    

In [11]:
json.dump(line_scores, open("line_scores.json", 'w'))